# 10_2_build_LGBM_TI.ipynb
Let LGBM learn the relationship between Path similarity (Levenshtein ratio) pattern and TI pattern.

- Using LGBM.
- Perform downsamling + vaging.
- After downsampling, the upper limit of the number of rows in the matrix is set to 1000.
- Separate the data after downsampling into training data and validation data.
- Learning is performed while tuning the parameters by optuna.integration.lightgbm.
- Bagging is done 10 times.

### input
- 5_X_train_test_datafile/train/X_train_PCA_TI.npz : Training data for explanatory variables in TI
- 5_X_train_test_datafile/train/Y_train_TI.npz : Training data for response variables in TI
- 10_build_LGBM_code/output/Train_Test_count_TI.csv : A file containing the ID of the TI that will create the model 

### output
- 11_LGBM/model_ti_*.pkl : LightGBM trained on training data

In [1]:
import pandas as pd
from imblearn.under_sampling import RandomUnderSampler
from scipy.sparse import load_npz
from sklearn.model_selection import train_test_split
import optuna.integration.lightgbm as lgb
import pickle
import warnings
warnings.filterwarnings('ignore')

In [2]:
Y_train = load_npz('../5_X_train_test_datafile/Y/Y_train_TI.npz')

In [3]:
Y_train.shape

(60732, 1684)

In [4]:
df_use = pd.read_csv("../7_Target_Drug_SE_TI_from_SIDER_DrugBank/Train_Test_count_TI.csv",header = 0, index_col=0)
df_use = df_use[df_use['use_ID']==1]

In [5]:
df_use

ID  train  test  use_ID
0        0  109.0  11.0       1
4        4  167.0  18.0       1
5        5  103.0  11.0       1
6        6   86.0   9.0       1
7        7   94.0  10.0       1
...    ...    ...   ...     ...
1672  1672  375.0  35.0       1
1675  1675  307.0  27.0       1
1676  1676  626.0  60.0       1
1678  1678  358.0  43.0       1
1679  1679   59.0   8.0       1

[1168 rows x 4 columns]

In [6]:
def bagging(seed):
    sampler = RandomUnderSampler(random_state=seed, replacement=True, sampling_strategy = 0.4)
    X_resampled, y_resampled = sampler.fit_resample(X_train.toarray(), y_train.toarray())
    if X_resampled.shape[0] > 1000:
        X_resampled, _, y_resampled, _ = train_test_split(X_resampled, y_resampled, train_size=1000, random_state=0, shuffle=True)
    
    X_train2, X_valid, y_train2, y_valid = train_test_split(X_resampled, y_resampled, test_size=0.2, random_state=0, shuffle=True)

    lgb_train = lgb.Dataset(X_train2, y_train2)
    lgb_eval = lgb.Dataset(X_valid, y_valid, reference=lgb_train)
    
    model = lgb.train(params,
                lgb_train,
                num_boost_round=200,
                valid_sets=[lgb_train, lgb_eval],
                early_stopping_rounds=50, verbose_eval=False,
                optuna_seed=0,
                verbosity = -1
               )
    
    with open('../11_LGBM_TI/model_ti_'+str(i)+'_'+str(seed)+'.pkl', 'wb') as f:
        pickle.dump(model, f)
    
    return model

In [7]:
list_0 = []

for i in df_use['ID']:
    X_train = load_npz('../5_X_train_test_datafile/train/X_train_Clustering_TI_'+ str(i) +'.npz')
    y_train = Y_train[:, i]
    
    params = {
    'objective': 'binary',
    'metric': 'binary_logloss',
    'verbosity' : -1,
    'deterministic':True,
    'force_row_wise':True
    }
      
    models = []

    try:
        for k in range(9):
            models.append(bagging(k))
    

    except:
        list_0.append(i)

[I 2022-01-30 14:07:34,147] A new study created in memory with name: no-name-8a190b68-9df5-402c-959c-96c3014391fa
bagging, val_score: 0.028539: 100%|####################################################| 10/10 [00:00<00:00, 15.62it/s]


feature_fraction, val_score: 0.116022: 100%|#############################################| 7/7 [00:00<00:00, 10.99it/s]


regularization_factors, val_score: 0.077918: 100%|#####################################| 20/20 [00:01<00:00, 15.62it/s]


bagging, val_score: 0.073577: 100%|####################################################| 10/10 [00:02<00:00,  4.84it/s]


feature_fraction, val_score: 0.153762: 100%|#############################################| 7/7 [00:01<00:00,  6.49it/s]


...

bagging, val_score: 0.082425: 100%|####################################################| 10/10 [00:01<00:00,  6.80it/s]


feature_fraction, val_score: 0.152562: 100%|#############################################| 7/7 [00:01<00:00,  4.79it/s]


regularization_factors, val_score: 0.071914: 100%|#####################################| 20/20 [00:04<00:00,  4.22it/s]


bagging, val_score: 0.102314: 100%|####################################################| 10/10 [00:01<00:00,  7.10it/s]


min_data_in_leaf, val_score: 0.361813: 100%|#############################################| 5/5 [00:00<00:00, 24.54it/s]


In [8]:
list_0

[]